In [73]:
%matplotlib inline
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function
import matplotlib.pyplot as plt
import tensorflow as tf
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.preprocessing import normalize
import cv2, os, math, time
from datetime import timedelta
from sklearn.utils import shuffle
from numpy.lib.stride_tricks import as_strided
from functools import reduce
from itertools import product

In [2]:
###Configuration
"""
Data Configurations/Paths
"""
img_dir="../../original_images/SD"
img_lbls=""
base_model = 'SD/sd_01_.ckpt'
model_20000 = 'SD/sd_20000.ckpt'
model_30000 = 'SD/sd_30000.ckpt'
model_40000 = 'SD/sd_40000.ckpt'
model_50000 = 'SD/sd_50000.ckpt'
model2_50000 = 'SD/sd2_50000.ckpt'

connected_model = 'SD/sd_conected.ckpt'

##
# Convolutional Layer 1.
filter_size1 = 4          # Convolution filters are 4 x 4 pixels.
num_filters1 = 16         # There are 16 of these filters.

# Convolutional Layer 2.
filter_size2 = 2          # Convolution filters are 2 x 2 pixels.
num_filters2 = 32         # There are 32 of these filters.

# Convolutional Layer 3.
filter_size3 = 2          # Convolution filters are 2 x 2 pixels.
num_filters3 = 64         # There are 64 of these filters.

# Convolutional Layer 4.
filter_size4 = 2          # Convolution filters are 2 x 2 pixels.
num_filters4 = 128         # There are 128 of these filters.

# Fully-connected layer.
fc_size = 2000             # Number of neurons in fully-connected layer.

# We know that images are 60 pixels in each dimension.
# img_size = 8 * 4

# Images are stored in one-dimensional arrays of this length.
img_size_flat = 10 * 10

# Number of colour channels for the images: 3 channel for RGB.
num_channels = 1

# Tuple with height and width of images used to reshape arrays.
img_shape = (10, 10, num_channels)

# Number of classes, one class for same or different image
num_classes = 4*2
patch_size = (2, 2)
npatches = 2

In [136]:
# def load_data(img_dir):
#         list_of_imgs = []
#         list_of_labels = []
#         list_same_diff = []
#         list_img_keys = []
#         for img in os.listdir(img_dir):
            
#             img_path = os.path.join(img_dir, img)
#             list_same_diff.append(int(os.listdir(img_path)[0]))
#             list_img_keys.append(img)
#             img_path = img_path + "/" + os.listdir(img_path)[0]
#             for img_label in os.listdir(img_path):
#                 img_data = os.path.join(img_path, img_label)
#                 if img_label == "img":
# #                     print(img_data + "/img.png")
#                     list_of_imgs.append(img_data + "/predicted_mask.png")
#                 else:
#                     list_of_labels.append([os.path.join(img_data, label) for label in os.listdir(img_data)])

#         data_imgs = np.array(list_of_imgs)
#         data_labels = np.array(list_of_labels)
#         data_same_diff = np.array(list_same_diff)
#         data_img_keys = np.array(list_img_keys)

#         return data_imgs, data_labels, data_same_diff, data_img_keys

    
# def get_batch_images(data, label, same_diff, img_keys, rshp, grey_scale):
#         list_of_imgs = []
#         list_of_labels = []
#         list_of_same_diff = []
#         list_of_img_keys = []
#         for img, lbl, img_type, img_key in zip(data, label, same_diff, img_keys):
#             orig_img = cv2.imread(img)
#             orig_lbl = cv2.imread(lbl)
#             if orig_img is None or orig_lbl is None:
#                     print ("Unable to read image{} or {}".format(img, lbl))
#                     continue
            
#             if (grey_scale):
#                 orig_lbl = rgb2grey(orig_lbl)

#             flattened_img = orig_img.flatten()
#             flattened_lbl = orig_lbl.flatten()

#             list_of_imgs.append(np.asarray(flattened_img, dtype=np.float32))
#             list_of_labels.append(np.asarray(flattened_lbl, dtype=np.float32))
#             list_of_same_diff.append(img_type)
#             list_of_img_keys.append(img_key)

#         data_labels = np.array(list_of_labels)
# #         print(data_labels.shape)
# #         print(rshp)
# #         reshaped_labels = np.reshape(data_labels, rshp)
# #         data_labels = np.squeeze(reshaped_labels[:, :, :1])
#         data_imgs = np.array(list_of_imgs)
#         data_img_type = np.array(list_of_same_diff)
#         data_img_keys = np.array(list_of_img_keys)
        
#         return data_imgs, data_labels, data_img_type, data_img_keys


def load_data(img_dir):
        list_of_orig_imgs = []
        list_of_pred_imgs = []
        list_of_labels = []
        list_same_diff = []
        list_img_keys = []
        for img in os.listdir(img_dir):
            
            img_path = os.path.join(img_dir, img)
            list_same_diff.append(int(os.listdir(img_path)[0]))
            list_img_keys.append(img)
            img_path = img_path + "/" + os.listdir(img_path)[0]
            for img_label in os.listdir(img_path):
                img_data = os.path.join(img_path, img_label)
                if img_label == "img":
#                     print(img_data + "/img.png")
                    list_of_orig_imgs.append(img_data + "/img.png")
                    list_of_pred_imgs.append(img_data + "/predicted_mask.png")
                else:
                    list_of_labels.append([os.path.join(img_data, label) for label in os.listdir(img_data)])

        data_imgs = np.array([list_of_orig_imgs, list_of_pred_imgs])
        data_labels = np.array(list_of_labels)
        data_same_diff = np.array(list_same_diff)
        data_img_keys = np.array(list_img_keys)

        return data_imgs, data_labels, data_same_diff, data_img_keys

    
def get_batch_images(data_orig, data_pred, label, same_diff, img_keys, rshp, grey_scale):
        list_of_orig_imgs = []
        list_of_pred_imgs = []
        list_of_labels = []
        list_of_same_diff = []
        list_of_img_keys = []
        for img_orig, img_pred, lbl, img_type, img_key in zip(data_orig, data_pred, label, same_diff, img_keys):
            if (grey_scale):
                orig_img = cv2.imread(img_orig)
                predicted_msk = cv2.imread(img_pred, cv2.IMREAD_GRAYSCALE)
            else:
                orig_img = cv2.imread(img[0])
                
            orig_lbl = cv2.imread(lbl)
            if orig_img is None or orig_lbl is None:
                    print ("Unable to read image{} or {}".format(img[0], lbl))
                    continue
            
            if (grey_scale):
                orig_lbl = rgb2grey(orig_lbl)

            flattened_orig_img = orig_img.flatten()
            flattened_pred_img = predicted_msk.flatten()
            flattened_lbl = orig_lbl.flatten()
            
            if grey_scale:
                flattened_lbl = np.reshape(flattened_lbl, [10, 10])
#                 print(flattened_lbl)
#                 flattened_lbl = normalize(flattened_lbl)
#                 print(flattened_lbl)
            
            list_of_orig_imgs.append(np.asarray(flattened_orig_img, dtype=np.float32))
            list_of_pred_imgs.append(np.asarray(flattened_pred_img, dtype=np.float32))
        
            list_of_labels.append(np.asarray(flattened_lbl, dtype=np.float32))
            list_of_same_diff.append(img_type)
            list_of_img_keys.append(img_key)

        data_labels = np.array(list_of_labels)
#         print(data_labels.shape)
#         print(rshp)
#         reshaped_labels = np.reshape(data_labels, rshp)
#         data_labels = np.squeeze(reshaped_labels[:, :, :1])
        data_imgs = np.array([list_of_orig_imgs, list_of_pred_imgs])
        data_img_type = np.array(list_of_same_diff)
        data_img_keys = np.array(list_of_img_keys)
        
        """this function call locates top left location of each patch in the mask and return. Comment it if contents are required."""
#         print(data_labels.shape)
#         data_labels = get_patch_loc(data_labels)
        
        return data_imgs, data_labels, data_img_type, data_img_keys

def get_batch_labels(label, same_diff, img_keys, rshp, grey_scale):
        list_of_labels = []
        list_of_same_diff = []
        list_of_img_keys = []
        for lbl, img_type, img_key in zip(label, same_diff, img_keys):
            orig_lbl = cv2.imread(lbl)
            if orig_lbl is None:
                    print ("Unable to read label{}".format(lbl))
                    continue
            
            if (grey_scale):
                orig_lbl = rgb2grey(orig_lbl)

            flattened_lbl = orig_lbl.flatten()
            
            if grey_scale:
                flattened_lbl = np.reshape(flattened_lbl, [10, 10])
            
            list_of_labels.append(np.asarray(flattened_lbl, dtype=np.float32))
            list_of_same_diff.append(img_type)
            list_of_img_keys.append(img_key)

        data_labels = np.array(list_of_labels)
        data_img_type = np.array(list_of_same_diff)
        data_img_keys = np.array(list_of_img_keys)
        
        """this function call locates top left location of each patch in the mask and return. Comment it if contents are required."""
#         print(data_labels.shape)
#         data_labels = get_patch_loc(data_labels)
        
        return data_labels, data_img_type, data_img_keys

def next_batch(num, data, labels):
    '''
    Return a total of `num` random samples and labels. 
    '''
    idx = np.arange(0 , len(data))
    np.random.shuffle(idx)
    idx = idx[:num]
    data_shuffle = [data[ i] for i in idx]
    labels_shuffle = [labels[ i] for i in idx]

    return np.asarray(data_shuffle), np.asarray(labels_shuffle)

def rgb2grey(rgb):
    return(np.dot(rgb[...,:3], [0.299, 0.587, 0.114]))

In [161]:
train_data, train_labels, img_type, img_keys = load_data(img_dir)

train_org = train_data[0, 0:2]
train_prd = train_data[1, 0:2]

merged_patch_lbls = train_labels[0:2, 0]
mask_lbls = train_labels[0:2, 3]
img_type_lbl = img_type[0:2]
img_key = img_keys[0:2]
dims = (2, 100, num_channels)
# print(train, merged_patch_lbls, mask_lbls)
train, labels, img_type_lbl, img_key = get_batch_images(train_org, train_prd, mask_lbls, img_type_lbl, img_key, dims, True)

In [162]:
mask_lbls[0]

'../../original_images/SD/15970/0/labels/mask_patch_1.png'

In [ ]:
def new_weights(shape, layer_name):
    initializer = tf.contrib.layers.xavier_initializer()
    return tf.Variable(initializer(shape), name=layer_name+'_W')

def new_bias(length, layer_name):
    return tf.Variable(tf.constant(0.05, shape=[length]), name=layer_name+'_b')

def new_conv_layer(input,
                   num_input_channels,
                   filter_size,
                   num_filters,
                   name_scope,
                   layer_name='',
                   use_pooling=True):

    with tf.name_scope(name_scope):
        shape = [filter_size, filter_size, num_input_channels, num_filters]
        weights = new_weights(shape, layer_name)
        biases = new_bias(num_filters, layer_name)

        layer = tf.add(tf.nn.conv2d(input=input, filter=weights, strides=[1,1,1,1], padding='SAME'), biases, name=layer_name)

        if use_pooling:
            layer = tf.nn.max_pool(value=layer,
                                   ksize=[1, 3, 3, 1],
                                   strides=[1, 2, 2, 1],
                                   padding='SAME', name=layer_name+'_max')
        layer = tf.nn.relu(layer, name=layer_name+'_activation')

    return layer, weights

def flatten_layer(layer):
    layer_shape = layer.get_shape()
    num_features = layer_shape[1:4].num_elements()
    layer_flat = tf.reshape(layer, [-1, num_features])
    
    return layer_flat, num_features

def new_fc_layer(input,
                num_inputs,
                num_outputs,
                name_scope,
                layer_name='',
                use_relu=True):
    
    with tf.name_scope(name_scope):
        weights = new_weights([num_inputs, num_outputs], layer_name)
        biases = new_bias(num_outputs, layer_name)

        layer = tf.add(tf.matmul(input, weights),biases,name=layer_name)
    #     layer = tf.matmul(input, weights) + biases

        if use_relu:
            layer = tf.nn.relu(layer, layer_name+'_activation')
    
    return layer

def normalise(tensor):
    return tf.div(
   tf.subtract(
      tensor, 
      tf.reduce_min(tensor)
   ), 
   tf.subtract(
      tf.reduce_max(tensor), 
      tf.reduce_min(tensor)
   )
)

In [ ]:
x = tf.placeholder(tf.float32, shape=[None, img_size_flat*num_channels], name='x')
x_image = tf.reshape(x, [-1, 10, 10, num_channels])
y_true = tf.placeholder(tf.float32, shape=[None, num_classes], name='y_true')
# y_true_cls = tf.argmax(y_true, axis=1)
y_true_cls = tf.placeholder(tf.float32, shape=[None, num_classes], name='y_true_cls')
x_image.shape, y_true

In [ ]:
import tensorflow as tf

# Input data
# input = tf.placeholder(tf.int32, [None, None])
# Submatrix dimension
# dims = tf.placeholder(tf.int32, [2])
# Number of top submatrices to find
# k = tf.placeholder(tf.int32, [])

input = tf.constant([
        [1, 1, 4, 4],
        [1, 1, 4, 4],
        [3, 3, 2, 2],
        [3, 3, 2, 2],
    ], dtype=tf.float32)

dims = tf.constant([2,2])
k = tf.constant(2)

input_shape = tf.shape(input)
rows, cols = input_shape[0], input_shape[1]
d_rows, d_cols = dims[0], dims[1]
subm_rows, subm_cols = rows - d_rows + 1, cols - d_cols + 1
# Index grids
ii, jj = tf.meshgrid(tf.range(subm_rows), tf.range(subm_cols), indexing='ij')
d_ii, d_jj = tf.meshgrid(tf.range(d_rows), tf.range(d_cols), indexing='ij')

# Add indices
subm_ii = ii[:, :, tf.newaxis, tf.newaxis] + d_ii
subm_jj = jj[:, :, tf.newaxis, tf.newaxis] + d_jj

ss = tf.stack([subm_ii, subm_jj], axis = -1)
# Make submatrices tensor
subm = tf.gather_nd(input, ss)

# Add submatrices
subm_sum = tf.reduce_sum(subm, axis=(2, 3))
# # Use TopK to find top submatrices
_, top_idx = tf.nn.top_k(tf.reshape(subm_sum, [-1]), tf.minimum(k, tf.size(subm_sum)))

# # Get row and column
top_row = top_idx // subm_cols
top_col = top_idx % subm_cols
result = tf.cast(tf.stack([top_row, top_col], axis=-1), dtype=tf.float32)

cost = tf.reduce_mean(tf.square(tf.constant([[2,0],[1,2]], dtype=tf.float32) - result))
optimizer = tf.train.AdamOptimizer(learning_rate=1e-4).minimize(cost)

with tf.Session() as sess:
    init = tf.global_variables_initializer()
    sess.run(init)
    print(sess.run(optimizer))

In [ ]:
import tensorflow as tf

# Input data
input = tf.placeholder(tf.float32, [None, None])
# Submatrix dimension
dims = tf.placeholder(tf.int32, [2])
# Number of top submatrices to find
k = tf.placeholder(tf.int32, [])
initializer = tf.contrib.layers.xavier_initializer()
# shape = [-1,8]
# outcome = tf.Variable(initializer(shape), name="outcome")

# input = tf.constant([
#         [1, 1, 4, 4],
#         [1, 1, 4, 4],
#         [3, 3, 2, 2],
#         [3, 3, 2, 2],
#     ])

# dims = tf.constant([2,2])
# k = tf.constant(2)

# with tf.Session() as sess:
#     init = tf.global_variables_initializer()
#     sess.run(init)

#     session.run(k)

# Sizes
# custom_input = tf.Variable(tf.shape(input), name='cmon')

# custom_input = input

my_inp = tf.reshape(input, [-1, 4,4])
input_shape = tf.shape(my_inp)
rows, cols = input_shape[1], input_shape[2]
d_rows, d_cols = dims[0], dims[1]
subm_rows, subm_cols = rows - d_rows + 1, cols - d_cols + 1

# # Index grids
ii, jj = tf.meshgrid(tf.range(subm_rows), tf.range(subm_cols), indexing='ij')
d_ii, d_jj = tf.meshgrid(tf.range(d_rows), tf.range(d_cols), indexing='ij')
# # # Add indices
subm_ii = ii[:, :, tf.newaxis, tf.newaxis] + d_ii
subm_jj = jj[:, :, tf.newaxis, tf.newaxis] + d_jj
# # Make submatrices tensor
subm = tf.gather_nd(my_inp[0,:,:], tf.stack([subm_ii, subm_jj], axis=-1))
# # Add submatrices
subm_sum = tf.reduce_sum(subm, axis=(2, 3))
# # Use TopK to find top submatrices
_, top_idx = tf.nn.top_k(tf.reshape(subm_sum, [-1]), tf.minimum(k, tf.size(subm_sum)))
# # Get row and column
top_row = top_idx // subm_cols
top_col = top_idx % subm_cols
result = tf.stack([top_row, top_col], axis=-1)
# # print(result)
# patches = tf.map_fn(lambda x: tf.slice(my_inp[0, :,:], x, patch_size), result, dtype=tf.float32)
# reshaped_patches = tf.squeeze(tf.reshape(patches, [tf.shape(patches)[0] * tf.shape(patches)[1] * tf.shape(patches)[2]]))
# outcome = tf.identity(reshaped_patches)
# reshaped_patches = reshaped_patches[-1, :]
# reshaped_patches = tf.squeeze(tf.reshape(reshaped_patches, [tf.shape(reshaped_patches)[0] * tf.shape(reshaped_patches)[1], 0]))

# Test
with tf.Session() as sess:
    mat = [
        [1, 1, 4, 4],
        [1, 1, 4, 4],
        [3, 3, 2, 2],
        [3, 3, 2, 2],
    ]
    
    mat_1 = np.reshape(mat, [-1, 16])
    print(sess.run(result, feed_dict={input: mat_1, dims: patch_size, k: npatches}))

In [62]:

img_x = cv2.imread("../../original_images/SD/15970/0/labels/mask.png")
img_grey = img_x[:, :, 0]
print(img_grey)
r = img_shape[0] - patch_size[0] + 1
c = img_shape[1] - patch_size[0] + 1

iter_o = np.array(list(product(range(0,patch_size[0]), range(0,patch_size[1]))))
left_corners = reduce(lambda x,y: np.multiply(x,y), map(lambda x, y: img_grey[x:x+r, y:y+c], iter_o[:, 0], iter_o[:, 1]))
left_top_locations = np.transpose(np.where(left_corners == 1))

print(left_top_locations)
print(np.array(mask_1, dtype=np.int32))

[[  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0 255 255   0   0   0   0   0 255 255]
 [  0 255 255   0   0   0   0   0 255 255]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]]
[[4 1]
 [4 8]]
[[  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0 255 255   0   0   0   0   0   0   0]
 [  0 255 255   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]
 [  0   0   0   0   0   0   0   0   0   0]]


### Generate 4 images, two with only left-top locations and two with complete patches

In [158]:
left_top_1 = np.zeros(100)
left_top_2 = np.zeros(100)
mask_1 = np.zeros(100)
mask_2 = np.zeros(100)
left_top_1 = np.reshape(left_top_1, [10,10])
left_top_2 = np.reshape(left_top_2, [10,10])
mask_1 = np.reshape(mask_1, [10,10])
mask_2 = np.reshape(mask_2, [10,10])

left_top_1[4, 1] = 255.
mask_1[4: 4+2, 1: 1+2] = 1
left_top_2[4,8] = 255.
mask_2[4:4+2, 8: 8+2] = 255.
print(mask_1.shape)
# see_output_grey(np.expand_dims(left_top_1, axis=0))
# see_output_grey(np.expand_dims(left_top_2, axis=0))
img = np.zeros([10,10],dtype=np.uint8)
img[4: 4+2, 1: 1+2, :] = 255
# print(rgb2grey(img))
plt.imshow(img)

# plt.imshow(rgb2grey(img))
#     plt.colorbar(img_x, orientation='horizontal')
# plt.show()
# 
# see_output_grey(np.expand_dims(mask_1, axis=0))
# see_output_grey(np.expand_dims(mask_2, axis=0))

# print(left_top_1)
# print(left_top_2)

(10, 10)


IndexError: too many indices for array

In [96]:
def determine_quad(left_top_locations, mid_point):
    box_1 = left_top_locations[0]
    box_2 = left_top_locations[1]
    box_quad = []
    quad_dict = {}
    
    for box in left_top_locations:
        if box[1] <= mid_point[0] and box[0] <= mid_point[1]: #both x and y are less than equal to the midpoint
    #         print("Quadrant II")
            box_quad.append(2)
        elif box[1] <= mid_point[0] and box[0] > mid_point[1]: #x is less than equal to x of midpoint but y is greater than y of midpoint
    #         print("Quadrant III")
            box_quad.append(3)
        elif box[1] > mid_point[0] and box[0] <= mid_point[1]: #x is greater than x of midpoint but y is less than equal to y of midpoint
    #         print("Quadrant I")
            box_quad.append(1)
        elif box[1] > mid_point[0] and box[0] > mid_point[1]: #x is greater than x of midpoint and y is greater than  y of midpoint
    #         print("Quadrant IV")
            box_quad.append(4)

    if (box_quad[0] == 2 and box_quad[1] == 1) or (box_quad[0] == 2 and box_quad[1] == 4) or (box_quad[0] == 3 and box_quad[1] == 1) or (box_quad[0] == 3 and box_quad[1] == 4):
    #     0 == Left and 1 == Right
#         print('Left box:', box_1)
#         print('Right box:', box_2)
        quad_dict['left_box'] = box_1
        quad_dict['right_box'] = box_2


    if (box_quad[0] == 1 and box_quad[1] == 2) or (box_quad[0] == 4 and box_quad[1] == 2) or (box_quad[0] == 1 and box_quad[1] == 3) or (box_quad[0] == 4 and box_quad[1] == 3):
    #    1 == Left and 0 == Right
#         print('Left box:', box_2)
#         print('Right box:', box_1)
        quad_dict['left_box'] = box_2
        quad_dict['right_box'] = box_1
        


    if (box_quad[0] == 1 and box_quad[1] == 4) or (box_quad[0] == 2 and box_quad[1] == 3):
    #    0 == Top and 1 == Bottom  
#         print('Top box:', box_1)
#         print('Bottom box:', box_2)
        quad_dict['top_box'] = box_1
        quad_dict['bottom_box'] = box_2

        
    if (box_quad[0] == 4 and box_quad[1] == 1) or (box_quad[0] == 3 and box_quad[1] == 2):
    #    1 == Top and 0 == Bottom
#         print('Top box:', box_2)
#         print('Bottom box:', box_1)
        quad_dict['top_box'] = box_2
        quad_dict['bottom_box'] = box_1

    return quad_dict
    

In [97]:
print(determine_quad(left_top_locations, mid_point))
box_1 = left_top_locations[0]
box_2 = left_top_locations[1]
mid_point = (4,4)
box_quad = []

for box in left_top_locations:
    if box[1] <= mid_point[0] and box[0] <= mid_point[1]: #both x and y are less than equal to the midpoint
#         print("Quadrant II")
        box_quad.append(2)
    elif box[1] <= mid_point[0] and box[0] > mid_point[1]: #x is less than equal to x of midpoint but y is greater than y of midpoint
#         print("Quadrant III")
        box_quad.append(3)
    elif box[1] > mid_point[0] and box[0] <= mid_point[1]: #x is greater than x of midpoint but y is less than equal to y of midpoint
#         print("Quadrant I")
        box_quad.append(1)
    elif box[1] > mid_point[0] and box[0] > mid_point[1]: #x is greater than x of midpoint and y is greater than  y of midpoint
#         print("Quadrant IV")
        box_quad.append(4)

if (box_quad[0] == 2 and box_quad[1] == 1) or (box_quad[0] == 2 and box_quad[1] == 4) or (box_quad[0] == 3 and box_quad[1] == 1) or (box_quad[0] == 3 and box_quad[1] == 4):
#     0 == Left and 1 == Right
    print('Left box:', box_1)
    print('Right box:', box_2)

    
if (box_quad[0] == 1 and box_quad[1] == 2) or (box_quad[0] == 4 and box_quad[1] == 2) or (box_quad[0] == 1 and box_quad[1] == 3) or (box_quad[0] == 4 and box_quad[1] == 3):
#    1 == Left and 0 == Right
    print('Left box:', box_2)
    print('Right box:', box_1)
    

if (box_quad[0] == 1 and box_quad[1] == 4) or (box_quad[0] == 2 and box_quad[1] == 3):
#    0 == Top and 1 == Bottom  
    print('Top box:', box_1)
    print('Bottom box:', box_2)

if (box_quad[0] == 4 and box_quad[1] == 1) or (box_quad[0] == 3 and box_quad[1] == 2):
#    1 == Top and 0 == Bottom
    print('Top box:', box_2)
    print('Bottom box:', box_1)

{'left_box': array([4, 1]), 'right_box': array([4, 8])}
Left box: [4 1]
Right box: [4 8]


In [ ]:
input = np.array([
    [[11, 12, 13], 
     [14, 15, 16]],
    [[21, 22, 23], 
     [24, 25, 26]],
    [[31, 32, 33], 
     [34, 35, 36]],
    [[41, 42, 43], 
     [44, 45, 46]],
    [[51, 52, 53], 
     [54, 55, 56]],
    ])

print(input.shape)
# tf.map_fn(lambda x: tf.slice(input, [1,0,0], [2,2,3]), result, dtype=tf.float32)
# s1 = tf.slice(input, [1, 0, ], [2, 2, 3])
x_image = tf.reshape(input, [1, 5, 2, 3], name='Images_2D')
s1 = x_image[:, 1:3, :2, :]
# s2 = tf.slice(input, [2, 0, 0], [3, 1, 2])
# s3 = tf.slice(input, [0, 0, 1], [4, 1, 1])
# s4 = tf.slice(input, [0, 0, 1], [1, 0, 1])
# s5 = tf.slice(input, [2, 0, 2], [-1, -1, -1]) # negative value means the function cutting tersors automatically
tf.global_variables_initializer()

with tf.Session() as s:
    print(s.run(s1))
#     print(s.run(s2)) 
#     print(s.run(s3)) 
#     print(s.run(s4)) 

In [ ]:
import tensorflow as tf

# Input data
input = tf.placeholder(tf.float32, [None, None])
# Submatrix dimension
dims = tf.placeholder(tf.int32, [2])
# Number of top submatrices to find
k = tf.placeholder(tf.int32, [])
initializer = tf.contrib.layers.xavier_initializer()
# shape = [-1,8]
# outcome = tf.Variable(initializer(shape), name="outcome")

# input = tf.constant([
#         [1, 1, 4, 4],
#         [1, 1, 4, 4],
#         [3, 3, 2, 2],
#         [3, 3, 2, 2],
#     ])

# dims = tf.constant([2,2])
# k = tf.constant(2)

# with tf.Session() as sess:
#     init = tf.global_variables_initializer()
#     sess.run(init)

#     session.run(k)

# Sizes
# custom_input = tf.Variable(tf.shape(input), name='cmon')

# custom_input = input

my_inp = tf.reshape(input, [-1, 10,10])
input_shape = tf.shape(my_inp)
rows, cols = input_shape[1], input_shape[2]
d_rows, d_cols = dims[0], dims[1]
subm_rows, subm_cols = rows - d_rows + 1, cols - d_cols + 1

# # Index grids
ii, jj = tf.meshgrid(tf.range(subm_rows), tf.range(subm_cols), indexing='ij')
d_ii, d_jj = tf.meshgrid(tf.range(d_rows), tf.range(d_cols), indexing='ij')
# # # Add indices
subm_ii = ii[:, :, tf.newaxis, tf.newaxis] + d_ii
subm_jj = jj[:, :, tf.newaxis, tf.newaxis] + d_jj

subm_st = tf.stack([subm_ii, subm_jj], axis=-1)

# # Make submatrices tensor
subm = tf.gather_nd(my_inp[0,:,:], tf.stack([subm_ii, subm_jj], axis=-1))
# # Add submatrices
subm_sum = tf.reduce_sum(subm, axis=(2, 3))
# # Use TopK to find top submatrices
_, top_idx = tf.nn.top_k(tf.reshape(subm_sum, [-1]), tf.minimum(k, tf.size(subm_sum)))
# # # Get row and column
top_row = top_idx // subm_cols
top_col = top_idx % subm_cols
result = tf.stack([top_row, top_col], axis=-1)
# orig_img_x = cv2.imread("../../original_images/SD/15970/0/img/img.png")
# orig_inp = tf.reshape(orig_img_x, [1, 10, 10, 3])
# patches = tf.squeeze(tf.map_fn(lambda x: tf.cast(orig_inp[:, x[0]:x[0] + patch_size[0], x[1]:x[1] + patch_size[1], :], dtype=tf.float32), result, dtype=tf.float32))
# patch_shape = tf.shape(patches)
# reshaped_patches = tf.reshape(patches, [-1, patch_shape[0] * patch_shape[1], patch_shape[2], patch_shape[3]])
# reshaped_patches = reshaped_patches[-1, :]
# reshaped_patches = tf.squeeze(tf.reshape(reshaped_patches, [tf.shape(reshaped_patches)[0] * tf.shape(reshaped_patches)[1], 0]))


# Test
with tf.Session() as sess:
    mat = [
        [1, 1, 4, 4],
        [1, 1, 4, 4],
        [3, 3, 2, 2],
        [3, 3, 2, 2],
    ]
    
    
    img_x = cv2.imread("../../original_images/SD/15970/0/labels/mask.png")
    img_x = rgb2grey(img_x)
    img_x = np.reshape(img_x, [10, 10])

#     orig_img_x = cv2.imread("../../original_images/SD/15970/0/img/img.png")
#     orig_inp = tf.reshape(orig_img_x, [1, 10, 10, 3])
#     print(orig_inp)
#     print(sess.run(tf.slice(orig_inp[-1, :,:, :], [4,8,0], [2,2,3])))

    
    
    
#     print(orig_img_x[4, 8, :3])
    
#     print(img_x)
#     print(orig_img_x)
# print(reshaped_img_x)
# print(reshaped_img_x.shape)
# see_output_grey(np.expand_dims(img_x, axis=0))    
# see_output_rgb(np.expand_dims(orig_img_x, axis=0))        
#     mat_1 = np.reshape(img_x, [-1, 10*10])
    print(sess.run(subm_st, feed_dict={input: img_x, dims: patch_size, k: npatches}))
#     print(sess.run(reshaped_patches, feed_dict={input: mat_1, dims: patch_size, k: npatches}))



In [ ]:
X = tf.constant([[[255., 255.],
  [255., 255.]],
 [[255., 255.],
  [255., 255.]]])

shape = X.get_shape().as_list()

reshaped_X = tf.squeeze(tf.reshape(X, [shape[0], shape[1], shape[2] , -1]))

with tf.Session() as sess:
    init = tf.global_variables_initializer()
    sess.run(init)
    print(session.run(X))


In [ ]:
import tensorflow as tf
import numpy as np

# build a tensor
x = np.arange(25)
x = np.reshape(x, [5, 5])
y = x + 4
three_d_array = np.stack([x, y], axis=2)
# make it into a tf tensor
three_d_tensor = tf.constant(three_d_array)

row_0, col_0 = 0, 0
row_1, col_1 = 0, 1
row_2, col_2 = 1, 0
row_3, col_3 = 1, 1
slice_tensor = tf.constant([
    [row_0, col_0],
    [row_1, col_1],
    [row_2, col_2],
    [row_3, col_3]
])
slices = tf.Variable(initial_value=slice_tensor)
gather_op = tf.gather_nd(three_d_tensor, slices)

with tf.Session() as sess:
    init = tf.global_variables_initializer()
    sess.run(init)

    submatrices = sess.run(gather_op)
    print(submatrices)
#     print(submatrices[0,:] == three_d_array[row_0, col_0])
#     print(submatrices[1,:] == three_d_array[row_1, col_1])
#     print(submatrices[2,:] == three_d_array[row_2, col_2])
#     print(submatrices[3,:] == three_d_array[row_3, col_3])
    
    


In [ ]:
import tensorflow as tf
import numpy as np

# build a tensor
x = np.arange(25)
x = np.reshape(x, [5, 5])
y = x + 4
three_d_array = np.stack([x, y], axis=2)
# just so you can see the shape its made of
print(np.all(x == three_d_array[:,:,0]))
print(np.all(y == three_d_array[:,:,1]))
# make it into a tf tensor
three_d_tensor = tf.constant(three_d_array)

# create a variable for tensor valued slice indices
row_0, col_0 = 0, 0
row_1, col_1 = 0, 1
row_2, col_2 = 1, 0
row_3, col_3 = 1, 1
slice_tensor = tf.constant([
    [row_0, col_0],
    [row_1, col_1],
    [row_2, col_2],
    [row_3, col_3]
])
slices = tf.Variable(initial_value=slice_tensor)

# op to get the sub matrices
gather_op = tf.gather_nd(three_d_tensor, slices)

with tf.Session() as sess:
    init = tf.global_variables_initializer()
    sess.run(init)

    submatrices = sess.run(gather_op)
    print(submatrices[0,:] == three_d_array[row_0, col_0])
    print(submatrices[1,:] == three_d_array[row_1, col_1])
    print(submatrices[2,:] == three_d_array[row_2, col_2])
    print(submatrices[3,:] == three_d_array[row_3, col_3])

    # shift down 2 along 2
    offset_top_left = tf.constant([2,2])
    update_variable_op = tf.assign(slices, slices + offset_top_left[None,:])
    sess.run(update_variable_op)
    submatrices = sess.run(gather_op)
    print(submatrices[0, :] == three_d_array[row_0 + 2, col_0 + 2])
    print(submatrices[1, :] == three_d_array[row_1 + 2, col_1 + 2])
    print(submatrices[2, :] == three_d_array[row_2 + 2, col_2 + 2])
    print(submatrices[3, :] == three_d_array[row_3 + 2, col_3 + 2])

In [ ]:
import tensorflow as tf
session = tf.Session()
# x = [[0, 0, 1, 1],
#      [0, 0, 1, 1],
#      [2, 2, 0, 0],
#      [2, 2, 0, 0]]
# X = tf.Variable(x, dtype=tf.float32)

# elems = tf.constant([[0,2]])
init = tf.global_variables_initializer()
session.run(init)
tf.map_fn(lambda s: tf.slice(tf.constant([[0,0,1,1],[0,0,1,1]], dtype=tf.float64), s, [2,2]), tf.constant([[0,2]], dtype=tf.int32), dtype=tf.float64).eval(session=session)
# tf.map_fn(lambda x: tf.slice(X, x, [2,2]), tf.constant([[0,2],[2,0]])).eval(session=session)
# X[elems[0]].eval(session=session)
# squares = tf.map_fn(lambda x: tf.shape(x), elems)
# squares.eval(session=session)

In [ ]:
import tensorflow as tf

x = [[0, 0, 1, 1],
     [0, 0, 1, 1],
     [2, 2, 0, 0],
     [2, 2, 0, 0]]
X = tf.Variable(x, dtype=tf.float32)
patch_starts = tf.constant([[0,2], [2,0]])
s1 = tf.map_fn(tf.slice(X, patch_starts[i], patch_size), patch_starts)
# s1 = tf.slice(X, [0,2], [2,2])


with tf.Session() as sess:
    init = tf.global_variables_initializer()
    sess.run(init)
    print(sess.run([s1]))

In [ ]:
i = tf.constant(1)
c = lambda i: tf.less(i, tf.shape(patch_starts)[0])
# patch_starts = tf.constant([[0,2], [1,2]])
# print(tf.less(i, tf.shape(patch_starts)[0]).eval(session=session))



# print(tf.less(i, 10).eval(session=session))
b = lambda i: tf.add(i, 1)
r = tf.while_loop(c, b, [1])

r.eval(session=session)

In [ ]:
all_ones = tf.ones([3, 3], tf.float32)
mat_box = tf.constant([[0.0,0.0,1.0,1.0], 
                       [0.0,0.0,1.0,1.0], 
                       [1.0,1.0,0.0,0.0], 
                       [1.0,1.0,0.0,0.0]], dtype=tf.float32, name="mat_box")
kernel = tf.reshape(all_ones, [3, 3, 1, 1], name='kernel')
# image  = tf.reshape(mat_box, [1, 4, 4, 1], name='image')

sliced_patches = tf.extract_image_patches(mat_box[tf.newaxis,:,:,tf.newaxis],
    [1, 3, 3, 1], [1, 1, 1, 1], [1, 1, 1, 1], padding='VALID')
sliced_patches = tf.reshape(sliced_patches, [-1, 3, 3])
cornered_patch = tf.scan(lambda a, b: tf.multiply(a, b), sliced_patches)[-1]

condition = tf.squeeze(tf.where(tf.equal(cornered_patch, [1.])))

print(condition.eval(session=session))


patches = tf.map_fn(lambda x: tf.slice(mat_box, x, patch_size), condition, dtype=tf.float32)
patches.eval(session=session)
# print(patch_starts.eval(session=session))
# print(mat_box[patch_start[0]:patch_start[0] + patch_size[0], :].eval(session=session))

# print(tf.gather(mat_box[:,], patch_start[0] + 2).eval(session=session))

# print(condition.eval(session=session))
# print(tf.where(cornered_patch = 1).eval(session=session))

# if len(np.where(cornered_image == 1)[0]) > 0:
# tmp_patch = reshaped_img[:, x[0]:x[0] + patch_size[0], y[0]:y[0]+patch_size[1], :]



# session.run(tf.global_variables_initializer())
# print(mat_box.eval(session=session))
# print(cornered_patch.eval(session=session))


In [ ]:
train_data, train_labels, img_type, img_keys = load_data(img_dir)

In [ ]:
# key = 36372
# img_keys[36372]
np.set_printoptions(suppress=True)
orig_img = cv2.imread("../../original_images/SD/1984/0/img/img.png", cv2.IMREAD_GRAYSCALE)
predicted_img = cv2.imread(train_data[36372], cv2.IMREAD_GRAYSCALE)
merged_img = cv2.imread(train_labels[36372, 0])

print(merged_img.shape)
print(merged_img)
print(predicted_img)
# print(orig_img)
# print(train_data[36372])
# orig_patches = train_labels[36372, 0]
# img_tensor = tf.constant(img_x, dtype=tf.float64)
# layer = normalise(img_tensor)
# layer.eval(session=session)

In [ ]:
# layer1_conv1, weights_conv1 = new_conv_layer(input=x_image,
#                                             num_input_channels=num_channels,
#                                             filter_size=filter_size1,
#                                             num_filters=num_filters1,
#                                              name_scope = 'cv',
#                                              layer_name='conv1',
#                                             use_pooling=True)

#     with tf.name_scope(name_scope):

# filter_size1 = 8          # Convolution filters are 4 x 4 pixels.
# num_filters1 = 8         # There are 16 of these filters.
# layer_name = "layer1"
# shape = [filter_size1, filter_size1, num_input_channels, num_filters1]

# initializer = tf.contrib.layers.xavier_initializer()
# weights1 = tf.Variable(initializer(shape), name=layer_name+'_W')
# biases1 = tf.Variable(tf.constant(0.05, shape=[length]), name=layer_name+'_b')

tf.random_normal

mat_box = tf.constant([[0.0,0.0,1.0,1.0], [0.0,0.0,1.0,1.0], [1.0,1.0,0.0,0.0], [1.0,1.0,0.0,0.0]], dtype=tf.float32, name="mat_box")

layer = normalise(x_image)

all_ones = tf.ones([3, 3], tf.float32)
kernel = tf.reshape(all_ones, [3, 3, 1, 1], name='kernel')
# image  = tf.reshape(mat_box, [1, 4, 4, 1], name='image')

sliced_patches = tf.extract_image_patches(mat_box[tf.newaxis,:,:,tf.newaxis],
    [1, 3, 3, 1], [1, 1, 1, 1], [1, 1, 1, 1], padding='VALID')
sliced_patches = tf.reshape(sliced_patches, [-1, 3, 3])
cornered_patch = tf.scan(lambda a, b: tf.multiply(a, b), sliced_patches)[-1]

condition = tf.squeeze(tf.where(tf.equal(cornered_patch, [1.])))

print(condition.eval(session=session))


patches = tf.map_fn(lambda x: tf.slice(mat_box, x, patch_size), condition, dtype=tf.float32)
patches.eval(session=session)




# layer = tf.add(tf.matmul(input, weights),biases,name=layer_name)
#     layer = tf.matmul(input, weights) + biases


#get patched corner



In [ ]:
layer_flat, num_features = flatten_layer(layer4_conv4)
y_pred_cls = layer_fc4

In [ ]:
layer_fc1 = new_fc_layer(input=layer_flat,
                         num_inputs=num_features,
                         num_outputs=fc_size+2,
                         name_scope = 'fc',
                         layer_name = 'fc1',
                         use_relu=True)




y_pred_cls = layer_fc4
y_pred = layer_fc4

In [ ]:
cost = tf.reduce_mean(tf.square(y_true - y_pred_cls))
optimizer = tf.train.AdamOptimizer(learning_rate=1e-4).minimize(cost)

## some more performance measures
correct_prediction = tf.equal(y_pred_cls, y_true)
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

### Experimental details of Graph

In [ ]:
session = tf.Session()
session.run(tf.global_variables_initializer())

train_data, train_labels, img_type, img_keys = load_data(img_dir)
train_labels = train_labels[:][:, 0]
total_imgs = len(train_data)
train_batch_size = 64

def optimize(num_epochs, save_model=True,save_name= "base_model",restore_model=False,restore_name=None):
    total_iterations = 0
    done_train_imgs = 0
    start_time = time.time()
    start_ = 0
    end_ = train_batch_size    
    plot_accuracy=[]
    plot_accuracy_epoch=[]
    plot_training_size=[]
    plot_training_size_epoch=[]
    saver = tf.train.Saver()
    sum_accuracy = 0.0
    n = 1
    
        #to save the model
    for i in range(0, num_epochs):   
        start_batch=0
        end_batch = train_batch_size
        
        print("Epoch:", i + 1)
        
        if restore_model==True:
            if restore_name==None:
                print("No model file specified")
                return
            else:
                saver.restore(session,restore_name)
        
        sum_accuracy = 0.0
        n = 1
        while end_batch < total_imgs:
            train = train_data[start_batch:end_batch]
            labels = train_labels[start_batch:end_batch]
            img_type_lbl = img_type[start_:end_]
            img_key = img_keys[start_:end_]
            dims = (len(train), num_classes, 1)
            train, labels, img_type_lbl, img_key = get_batch_images(train, labels, img_type_lbl, img_key, dims)
            if not len(train) and not len(labels):
                print("All images have been processed.")
                break;

            x_batch, y_true_batch = next_batch(len(train), train, labels)
            feed_dict_train = {x: x_batch,
                       y_true: y_true_batch}
            
            session.run(optimizer, feed_dict=feed_dict_train)
    
            acc,co = session.run([accuracy, cost], feed_dict=feed_dict_train)
            sum_accuracy += acc
            n+=1
            msg = "Optimization Iteration: {0:>6}, Training Accuracy: {1:>6.1%}, Loss: {2:>.4f}"
            print(msg.format(end_batch + 1, acc, co))
            if i == num_epochs - 1:
                plot_accuracy.append(acc)
                plot_training_size.append(end_batch + 1)

            start_batch += train_batch_size
            end_batch += train_batch_size
    
        if save_model==True:
            if save_name==None:
                print("No model specified, model not being saved")
                return
            else:
                save_path = saver.save(session, save_name)
                restore_model = True
                print("Model saved in file: %s" % save_name)
        plot_accuracy_epoch.append(sum_accuracy/n)
        plot_training_size_epoch.append(i + 1)
    
    end_time = time.time()
    # Difference between start and end-times.
    time_dif = end_time - start_time

    # Print the time-usage.
    print("Time usage: " + str(timedelta(seconds=int(round(time_dif)))))  
    print(plot_accuracy)
    print(plot_training_size)
    print(plot_accuracy_epoch)
    print(plot_training_size_epoch)

In [ ]:
save_model = True
save_name = model2_50000
restore_model=False
restore_name=model2_50000

optimize(50, save_model=True,save_name=model2_50000,restore_model=False,restore_name=model2_50000)

In [137]:
def restore_see_layer(ix, model_name=None, var_name=None):
    with tf.Session('', tf.Graph()) as s:
        with s.graph.as_default():
            if ((model_name != None) and var_name != None):
                saver = tf.train.import_meta_graph(model_name+".meta")
                saver.restore(s, model_name)
                fd = {'x:0':ix}
                var_name=var_name+":0"
                    
                result = 0
                result = s.run(var_name, feed_dict=fd)
    return result

def see_output_rgb(iNp,depth_filter_to_see=0,cmap="gray",figsize=(4,4)):
    img_x = iNp[0,:,:,:]
    fig = plt.figure(figsize=figsize)
    plt.imshow(img_x, interpolation='none', aspect='auto')
#     plt.colorbar(img_x, orientation='horizontal')
    plt.show()
    
def see_output_grey(iNp,depth_filter_to_see=0,cmap="gray",figsize=(4,4)):
    img_x = iNp[0,:,:]
    fig = plt.figure(figsize=figsize)
    plt.imshow(img_x, interpolation='none', aspect='auto')
#     plt.colorbar(img_x, orientation='horizontal')
    plt.show()

    
def get_patch_corner(img):
    r = img_shape[0]
    c = img_shape[1]
    rp = patch_size[0]
    cp = patch_size[1]
    conv_r= r - rp + 1
    conv_c = c - cp + 1

    all_ones = np.ones((conv_r,conv_c))
    for i in range(0, rp):
        for j in range(0, cp):
    #         print(np_m[0+i:conv_r+i, 0+j:conv_c+j])
            all_ones = np.multiply(all_ones, img[0+i:conv_r+i, 0+j:conv_c+j])

    return(all_ones)



def normalized(arr):
    return (arr - np.min(arr))/(np.max(arr) - np.min(arr))

def save_patch_images(img_x1, lbl_x1, index):
    if not os.path.exists('./SD/patched_images/' + str(index)):
        os.makedirs('./SD/patched_images/' + str(index))
        os.makedirs('./SD/patched_images/' + str(index) + "/" + str(lbl_x1))
        
    plt.imsave('./SD/patched_images/' + str(index) + "/" + str(lbl_x1) + '/img.png', np.squeeze(img_x1))
    

def predict_nd_save(train, labels, img_type_lbl, img_key, start_idx):

    for index in range(0, len(train)):
        img_x = train[index:index+1, :]
        lbl_x = labels[index:index+1, :]
        img_type_x = img_type_lbl[index]
        img_key_x = img_key[index]
        prediction = restore_see_layer(ix=img_x,model_name=model_50000,var_name='fc_3/fc4')
        prediction = np.reshape(prediction, (1, 10,10, 1))   
        save_patch_images(prediction, img_type_x, img_key_x)
            
# def save_patch_images(img_x1, lbl_x1, index):
#     if not os.path.exists('./SD/patched_images/' + str(index)):
#         os.makedirs('./SD/patched_images/' + str(index))
#         os.makedirs('./SD/patched_images/' + str(index) + "/" + str(lbl_x1))
        

#     plt.imsave('./SD/patched_images/' + str(index) + "/" + str(lbl_x1) + '/img.png', np.squeeze(img_x1))

def determine_quad(left_top_locations, mid_point):
    box_1 = left_top_locations[0]
    box_2 = left_top_locations[1]
    box_quad = []
    quad_dict = {}
    
    for box in left_top_locations:
        if box[1] <= mid_point[0] and box[0] <= mid_point[1]: #both x and y are less than equal to the midpoint
    #         print("Quadrant II")
            box_quad.append(2)
        elif box[1] <= mid_point[0] and box[0] > mid_point[1]: #x is less than equal to x of midpoint but y is greater than y of midpoint
    #         print("Quadrant III")
            box_quad.append(3)
        elif box[1] > mid_point[0] and box[0] <= mid_point[1]: #x is greater than x of midpoint but y is less than equal to y of midpoint
    #         print("Quadrant I")
            box_quad.append(1)
        elif box[1] > mid_point[0] and box[0] > mid_point[1]: #x is greater than x of midpoint and y is greater than  y of midpoint
    #         print("Quadrant IV")
            box_quad.append(4)

#     print('quadrant:', box_quad)
    
    if box_quad[0] == box_quad[1]:
        if abs(box_1[1] - box_2[1]) > abs(box_1[0] - box_2[0]): #top/bottom case
            if box_1[1] < box_2[1]:
                quad_dict['left_box'] = box_1
                quad_dict['right_box'] = box_2
            else:
                quad_dict['left_box'] = box_2
                quad_dict['right_box'] = box_1
                
        else: #left/right case
            if box_1[0] < box_2[0]:
                quad_dict['top_box'] = box_1
                quad_dict['bottom_box'] = box_2
            else:
                quad_dict['top_box'] = box_2
                quad_dict['bottom_box'] = box_1
                
    
    if (box_quad[0] == 2 and box_quad[1] == 1) or (box_quad[0] == 2 and box_quad[1] == 4) or (box_quad[0] == 3 and box_quad[1] == 1) or (box_quad[0] == 3 and box_quad[1] == 4):
    #     0 == Left and 1 == Right
#         print('Left box:', box_1)
#         print('Right box:', box_2)
        quad_dict['left_box'] = box_1
        quad_dict['right_box'] = box_2


    if (box_quad[0] == 1 and box_quad[1] == 2) or (box_quad[0] == 4 and box_quad[1] == 2) or (box_quad[0] == 1 and box_quad[1] == 3) or (box_quad[0] == 4 and box_quad[1] == 3):
    #    1 == Left and 0 == Right
#         print('Left box:', box_2)
#         print('Right box:', box_1)
        quad_dict['left_box'] = box_2
        quad_dict['right_box'] = box_1
        


    if (box_quad[0] == 1 and box_quad[1] == 4) or (box_quad[0] == 2 and box_quad[1] == 3):
    #    0 == Top and 1 == Bottom  
#         print('Top box:', box_1)
#         print('Bottom box:', box_2)
        quad_dict['top_box'] = box_1
        quad_dict['bottom_box'] = box_2

        
    if (box_quad[0] == 4 and box_quad[1] == 1) or (box_quad[0] == 3 and box_quad[1] == 2):
    #    1 == Top and 0 == Bottom
#         print('Top box:', box_2)
#         print('Bottom box:', box_1)
        quad_dict['top_box'] = box_2
        quad_dict['bottom_box'] = box_1

    return quad_dict

def get_patch_loc(img):
    img = np.squeeze(img)
    img[np.where(img == 255)] = 1.
    r = img_shape[0] - patch_size[0] + 1
    c = img_shape[1] - patch_size[0] + 1

    iter_o = np.array(list(product(range(0,patch_size[0]), range(0,patch_size[1]))))
    left_corners = reduce(lambda x,y: np.multiply(x,y), map(lambda x, y: img[x:x+r, y:y+c], iter_o[:, 0], iter_o[:, 1]))
    left_top_locations = np.transpose(np.where(left_corners == 1))
    left_top_locations = np.array(left_top_locations, dtype=np.int32)
    return left_top_locations

def sep_boxes(labels, img_type_lbl, img_key, start_idx):
    patched_images = []
    mid_point = (4,4)
    for index in range(0, len(labels)):
        lbl_x = labels[index:index+1, :]
        img_type_x = img_type_lbl[index]
        img_key_x = img_key[index]
        top_left_loc = get_patch_loc(lbl_x)
#         see_output_grey(np.expand_dims(np.squeeze(lbl_x), axis=0))
        quad_dict = determine_quad(top_left_loc, mid_point)
#         print(quad_dict)
        
        left_top_1 = np.zeros(100)
        left_top_2 = np.zeros(100)
        mask_1 = np.zeros(100)
        mask_2 = np.zeros(100)
        left_top_1 = np.reshape(left_top_1, [10,10])
        left_top_2 = np.reshape(left_top_2, [10,10])
        mask_1 = np.reshape(mask_1, [10,10])
        mask_2 = np.reshape(mask_2, [10,10])

# {'left_box': array([0, 1], dtype=int32), 'right_box': array([2, 6], dtype=int32)}
# {'top_box': array([1, 1], dtype=int32), 'bottom_box': array([6, 1], dtype=int32)}        
        
        if 'left_box' in quad_dict:
            coords = quad_dict['left_box']
            left_top_1[coords[0], coords[1]] = 255.
            mask_1[coords[0]: coords[0]+2, coords[1]: coords[1]+2] = 255.
            coords = quad_dict['right_box']
            left_top_2[coords[0], coords[1]] = 255.
            mask_2[coords[0]:coords[0]+2, coords[1]: coords[1]+2] = 255.
        elif 'top_box' in quad_dict:
            coords = quad_dict['top_box']
            left_top_1[coords[0], coords[1]] = 255.
            mask_1[coords[0]: coords[0]+2, coords[1]: coords[1]+2] = 255.
            coords = quad_dict['bottom_box']
            left_top_2[coords[0], coords[1]] = 255.
            mask_2[coords[0]:coords[0]+2, coords[1]: coords[1]+2] = 255.
            
#         see_output_grey(np.expand_dims(left_top_1, axis=0))
#         see_output_grey(np.expand_dims(left_top_2, axis=0))
#         see_output_grey(np.expand_dims(mask_1, axis=0))
#         see_output_grey(np.expand_dims(mask_2, axis=0))
        
#         img_x = cv2.imread("../../original_images/SD/15970/0/img/img.png")
        plt.imsave('../../original_images/SD/' + str(img_key_x) + "/" + str(img_type_x) + '/labels/left_top_point_1.png' , np.squeeze(left_top_1))
        plt.imsave('../../original_images/SD/' + str(img_key_x) + "/" + str(img_type_x) + '/labels/left_top_point_2.png' , np.squeeze(left_top_2))
        plt.imsave('../../original_images/SD/' + str(img_key_x) + "/" + str(img_type_x) + '/labels/mask_patch_1.png' , np.squeeze(mask_1))
        plt.imsave('../../original_images/SD/' + str(img_key_x) + "/" + str(img_type_x) + '/labels/mask_patch_2.png' , np.squeeze(mask_2))

        
#         save_patch_images(tmp_patch, img_type_x, img_key_x)

#         patched_images.append(tmp_patch)
#         tmp_patch = []
        
    return patched_images    

    
def extract_combine_patches(train, labels, img_type_lbl, img_key, start_idx):
    patched_images = []
    
    for index in range(0, len(train)):
#         print(index)
        img_x = train[index:index+1, :]
        lbl_x = labels[index:index+1, :]
        img_type_x = img_type_lbl[index]
        img_key_x = img_key[index]
#         output_cl1 = restore_see_layer(ix=img_x,model_name=model_50000,var_name='fc_3/fc4')
#         output_fc4_w = restore_see_layer(ix=img_x,model_name=model_50000,var_name='fc_3/fc4_W')
#         normalized_output = np.rint(normalized(output_cl1))
#         np_m = np.squeeze(np.reshape(normalized_output, (1,10,10,1)))
#         cornered_image = get_patch_corner(np_m)

#         reshaped_img = np.reshape(img_x, (1, 10,10, 3))
#         x, y = np.where(cornered_image == 1)
        
#         if len(np.where(cornered_image == 1)[0]) > 0:
#             tmp_patch = reshaped_img[:, x[0]:x[0] + patch_size[0], y[0]:y[0]+patch_size[1], :]
#         else:
#             continue
            
#         for idx in range(1, len(np.where(cornered_image == 1)[0])):
# #             print("index:", idx)
# #             print("X:", x)
# #             print("Y:", y)
# #             print("reshaped image:", reshaped_img)
#             tmp_patch1 = reshaped_img[:, x[idx]:x[idx] + patch_size[0], y[idx]:y[idx]+patch_size[1], :]
#             tmp_patch = np.expand_dims(np.concatenate((np.squeeze(tmp_patch), np.squeeze(tmp_patch1)), axis=0), axis=0)
        
#         print(tmp_patch.shape)
#         save_patch_images(tmp_patch, img_type_x, start_idx + index)
        save_patch_images(tmp_patch, img_type_x, img_key_x)

        patched_images.append(tmp_patch)
        tmp_patch = []
        
    return patched_images

### Separate boxes

In [138]:
train_data, train_labels, img_type, img_keys = load_data(img_dir)
# train_orgs = train_data[0, :]
# train_prds = train_data[1, :]
train_mask_labels = train_labels[:, 1]
batch_s = 64
total_iterations = 0
start_ = 0
end_ = batch_s
np.set_printoptions(suppress=True)
while True:

#     train_org = train_orgs[start_:end_]
#     train_prd = train_prds[start_:end_]
    mask_lbls = train_mask_labels[start_:end_]
    img_type_lbl = img_type[start_:end_]
    img_key = img_keys[start_:end_]
    dims = (batch_s, num_classes, num_channels)
    labels, img_type_lbl, img_key = get_batch_labels(mask_lbls, img_type_lbl, img_key, dims, True)
    patch_images = sep_boxes(labels, img_type_lbl, img_key, start_)
    
    #do my stuff
    if len(train_mask_labels) < start_ + batch_s:
        print("{} Images have been processed.".format(total_iterations))
        break
    
    total_iterations +=batch_s
    start_ = end_
    end_ = end_ + batch_s

49984 Images have been processed.


In [ ]:
train_data, train_labels, img_type, img_keys = load_data(img_dir)
train_mask_labels = train_labels[:][:, 1]
train_patch_labels = train_labels[:][:, 0]

batch_s = 64
total_iterations = 0
start_ = 0
end_ = batch_s
np.set_printoptions(suppress=True)

if not os.path.exists('./SD/predicted_mask'):
    os.makedirs('./SD/predicted_mask')

while True:
    train = train_data[start_:end_]
    labels = train_mask_labels[start_:end_]
    img_type_lbl = img_type[start_:end_]
    img_key = img_keys[start_:end_]
    dims = (batch_s, num_classes, num_channels)
    train, labels, img_type_lbl, img_key = get_batch_images(train, labels, img_type_lbl, img_key, dims)
    predict_nd_save(train, labels, img_type_lbl, img_key, start_)
    
    #do my stuff
    if len(train_data) < start_ + batch_s:
        print("{} Images have been processed.".format(total_iterations))
        break
    
    total_iterations +=batch_s
    start_ = end_
    end_ = end_ + batch_s    

In [ ]:
train_data, train_labels, img_type, img_keys = load_data(img_dir)
train_mask_labels = train_labels[:][:, 1]
train_patch_labels = train_labels[:][:, 0]
batch_s = 64
total_iterations = 0
start_ = 0
end_ = batch_s
np.set_printoptions(suppress=True)

if not os.path.exists('./SD/patched_images'):
    os.makedirs('./SD/patched_images')

while True:

    train = train_data[start_:end_]
    labels = train_labels[start_:end_]
    img_type_lbl = img_type[start_:end_]
    img_key = img_keys[start_:end_]
    dims = (batch_s, num_classes, num_channels)
    train, labels, img_type_lbl, img_key = get_batch_images(train, labels, img_type_lbl, img_key, dims)
    patch_images = extract_combine_patches(train, labels, img_type_lbl, img_key, start_)
    
    #do my stuff
    if len(train_data) < start_ + batch_s:
        print("{} Images have been processed.".format(total_iterations))
        break
    
    total_iterations +=batch_s
    start_ = end_
    end_ = end_ + batch_s

In [ ]:
see_output(np.expand_dims(orig_img, axis=0))
see_output(np.expand_dims(orig_lbl, axis=0))

In [ ]:
train_data, train_labels, img_type, img_keys = load_data(img_dir)

In [ ]:
train = train_data[0:1]
labels = train_labels[0:1, 0]
labels
img_type_lbl = img_type[0:1]
img_key = img_keys[0:1]
dims = (1, num_classes, num_channels)
train, labels, img_type_lbl, img_key = get_batch_images(train, labels, img_type_lbl, img_key, dims, False)

# train[0:1]
# img_x = cv2.imread("../../original_images/SD/15970/0/img/predicted_mask.png")

# img_x = np.expand_dims(img_x[:,:,0].flatten(), axis=0)

np.set_printoptions(suppress=True)
output_cl1 = restore_see_layer(ix=img_x,model_name=model_50000,var_name='fc_3/fc4')
print(output_cl1)
# show_img = np.expand_dims(np.reshape(output_cl1, (4,2,3)), axis=0)

In [ ]:
def see_output(iNp,depth_filter_to_see=0,cmap="gray",figsize=(4,4)):
    img_x = iNp[0,:,:]
    fig = plt.figure(figsize=figsize)
    plt.imshow(img_x, interpolation='none', aspect='auto')
#     plt.colorbar(img_x, orientation='horizontal')
    plt.show()

In [ ]:
img_x = cv2.imread("../../original_images/SD/15970/0/img/img.png")
img_x = rgb2grey(img_x)
# img_x = np.reshape(img_x, [10, 10, ])
print(img_x.shape)
# print(reshaped_img_x)
# print(reshaped_img_x.shape)
# see_output(np.expand_dims(img_x, axis=0))

In [47]:
import tensorflow as tf

# Input data
input = tf.placeholder(tf.float32, [None])
orig_input = tf.placeholder(tf.float32, [None])
# Submatrix dimension
dims = tf.placeholder(tf.int32, [2])
# Number of top submatrices to find
k = tf.placeholder(tf.int32, [])

my_inp = tf.reshape(input, [-1, 10,10])
input_shape = tf.shape(my_inp)
rows, cols = input_shape[1], input_shape[2]
d_rows, d_cols = dims[0], dims[1]
subm_rows, subm_cols = rows - d_rows + 1, cols - d_cols + 1

# # Index grids
ii, jj = tf.meshgrid(tf.range(subm_rows), tf.range(subm_cols), indexing='ij')
d_ii, d_jj = tf.meshgrid(tf.range(d_rows), tf.range(d_cols), indexing='ij')
# # # Add indices
subm_ii = ii[:, :, tf.newaxis, tf.newaxis] + d_ii
subm_jj = jj[:, :, tf.newaxis, tf.newaxis] + d_jj


subm_st = tf.stack([subm_ii, subm_jj], axis=-1)
# # Make submatrices tensor
subm = tf.gather_nd(my_inp[0,:,:], tf.stack([subm_ii, subm_jj], axis=-1))
# # Add submatrices
subm_sum = tf.reduce_sum(subm, axis=(2, 3))
# # Use TopK to find top submatrices
_, top_idx = tf.nn.top_k(tf.reshape(subm_sum, [-1]), tf.minimum(k, tf.size(subm_sum)))
# # # Get row and column
top_row = top_idx // subm_cols
top_col = top_idx % subm_cols
result = tf.stack([top_row, top_col], axis=-1)

# orig_img_x = cv2.imread("../../original_images/SD/15970/0/img/img.png")
orig_inp = tf.reshape(orig_input, [1, 10, 10, 3])
patches = tf.squeeze(tf.map_fn(lambda x: tf.cast(orig_inp[:, x[0]:x[0] + patch_size[0], x[1]:x[1] + patch_size[1], :], dtype=tf.float32), result, dtype=tf.float32))
patch_shape = tf.shape(patches)
reshaped_patches = tf.reshape(patches, [-1, patch_shape[0] * patch_shape[1], patch_shape[2], patch_shape[3]])

# Test
with tf.Session() as sess1:
#     orig_x = cv2.imread("../../original_images/SD/15970/0/img/img.png")
#     orig_x = np.reshape(orig_x, [-1])
#     img_x = cv2.imread("../../original_images/SD/15970/0/img/predicted_mask.png")
#     img_x = rgb2grey(img_x)
#     img_x = np.reshape(img_x, [-1])
#     print(orig_x.shape, img_x.shape)
#     resh_patches, orig_inp = sess1.run([reshaped_patches, orig_inp], feed_dict={input: img_x, orig_input:orig_x,  dims: patch_size, k: npatches})
#     print(resh_patches, orig_inp)
    train_data, train_labels, img_type, img_keys = load_data(img_dir)
    train_orgs = train_data[0, :]
#     print(train_org.shape)
    train_prds = train_data[1, :]
    train_mask_labels = train_labels[:, 1]
#     train_patch_labels = train_labels[:][:, 0]
    img_type_lbl = img_type[:]
    img_key = img_keys[:]
    
    batch_s = 64
    total_iterations = 0
    start_ = 0
    end_ = batch_s
    np.set_printoptions(suppress=True)

    if not os.path.exists('./SD/patched_images'):
        os.makedirs('./SD/patched_images')

        
    while True:
        train_org = train_orgs[start_:end_]
        train_prd = train_prds[start_:end_]
        mask_lbls = train_mask_labels[start_:end_]
        img_type_lbl = img_type[start_:end_]
        img_key = img_keys[start_:end_]
        dims1 = (batch_s, num_classes, num_channels)
        train, labels, img_type_lbl, img_key = get_batch_images(train_org, train_prd, mask_lbls, img_type_lbl, img_key, dims1, True)
        print(train.shape)
        for index in range(0, len(train[0])):
            orig_x = train[0, index:index+1][0]
            img_x = train[1, index:index+1][0]
            lbl_x = labels[index:index+1]
            img_type_x = img_type_lbl[index:index+1][0]
            img_key_x = img_key[index:index+1][0]
            
#             print(orig_x.shape, img_x.shape)
        
#             orig_x = cv2.imread("../../original_images/SD/15970/0/img/img.png")
#             orig_x = np.reshape(orig_x, [-1])
#             img_x = cv2.imread("../../original_images/SD/15970/0/img/predicted_mask.png")
#             img_x = rgb2grey(img_x)
#             img_x = np.reshape(img_x, [-1])
#             print(orig_x.shape, img_x.shape)
            
            resh_patches = sess1.run(reshaped_patches, feed_dict={input: img_x, orig_input:orig_x,  dims: patch_size, k: npatches})
#             print(resh_patches)
            save_patch_images(resh_patches, img_type_x, img_key_x)
        
        if len(train_orgs) < start_ + batch_s:
            print("{} Images have been processed.".format(total_iterations))
            break

        total_iterations +=batch_s
        start_ = end_
        end_ = end_ + batch_s    
    

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


(2, 64)


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

(2, 64)


...

(2, 64)


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

(2, 64)


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


AttributeError: 'NoneType' object has no attribute 'flatten'